In [54]:
import pandas as pd
import json
import gzip
import numpy as np
import scipy
from scipy.sparse import csr_matrix
from scipy.sparse import csc_matrix
from scipy.sparse.linalg import svds
import sklearn
from sklearn.neighbors import NearestNeighbors
from sklearn.preprocessing import normalize
import csv
from sparsesvd import sparsesvd
import math
import operator

In [55]:
def unzip_json(filename):
    
    print('Unzipping json file...')
    
    unzipped_data = pd.read_json(gzip.open(filename))
    
    return unzipped_data

In [56]:
# Output json training data as a Pandas dataframe.
def json_to_df(file_name):

    print('Converting json file to dataframe...')

    try:
        training_data = pd.read_json(file_name, lines=True)
        return training_data
    except:
        print('Please try another file name.')

        return None

In [57]:
# training_df = json_to_df('reviews.training.json')

In [58]:
# dev_df = json_to_df('reviews.dev.json')

In [59]:
def convert_to_csv(dataframe, desired_filename):

    print('Converting dataframe to csv: ' + desired_filename + '...')

    try:
        return dataframe.to_csv(desired_filename, index=False)
    except:
        print('Please try another dataframe or file name.')

    return None

In [60]:
# Training file to CSV
# convert_to_csv(training_df[['reviewerID', 'asin', 'overall']].head(5000), 'reviews.training.shortened.csv')

In [61]:
# Development file to CSV.
# convert_to_csv(dev_df[['reviewerID', 'asin', 'overall']], 'reviews.dev.csv')

In [62]:
# Returns dictionaries with unique users and products as keys and unique ints as values.
def create_user_product_dicts(filename):

    print('Creating dictionaries from CSV for unique users and products...')

    user_dict = {}
    product_dict = {}
    user_count = 0
    product_count = 0

    with open(filename, 'r') as train_file:
        file_reader=csv.reader(train_file, delimiter=',')
        next(file_reader, None)

        for row in file_reader:
            if row[0] not in user_dict:
                user_dict[row[0]] = user_count
                user_count += 1
            if row[1] not in product_dict:
                product_dict[row[1]] = product_count
                product_count += 1

    return user_dict, product_dict, user_count, product_count

In [63]:
user_dict, product_dict, user_count, product_count = create_user_product_dicts('reviews.training.shortened.csv')

Creating dictionaries from CSV for unique users and products...


In [64]:
def training_mtx(filename, user_dict, product_dict):

        print('Creating a dense matrix from training data...')

        num_user_ids = len(user_dict)
        num_product_ids = len(product_dict)

        dense_matrix = np.zeros(shape=(num_user_ids, num_product_ids), dtype=np.float32)

        with open(filename, 'r') as train_file:
            matrix_reader = csv.reader(train_file, delimiter=',')
            next(matrix_reader, None)
            for row in matrix_reader:
                dense_matrix[user_dict[row[0]], product_dict[row[1]]] = float(row[2])

        return dense_matrix

In [65]:
training_matrix = training_mtx('reviews.training.shortened.csv', user_dict, product_dict)

Creating a dense matrix from training data...


In [66]:
training_matrix

array([[4., 0., 0., ..., 0., 0., 0.],
       [0., 5., 0., ..., 0., 0., 0.],
       [0., 0., 5., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 4., 0., 0.],
       [0., 0., 0., ..., 0., 4., 0.],
       [0., 0., 0., ..., 0., 0., 2.]], dtype=float32)

In [67]:
training_matrix.shape

(4426, 4053)

In [68]:
# Outputs dictionaries with unique test users and test products.
def get_test_users_products(filename, training_user_dict, training_product_dict):

    print('Importing test users and products...')

    test_user_count = len(training_user_dict)
    test_product_count = len(training_product_dict)
    test_user_dict = training_user_dict.copy()
    test_product_dict = training_product_dict.copy()

    with open(filename, 'r') as test_file:
        test_reader = csv.reader(test_file, delimiter=',')
        next(test_reader, None)

        for row in test_reader:
            # Add unique users to test_user dictionary.
            if row[1] not in test_user_dict:
                test_user_dict[row[0]] = test_user_count
                test_user_count += 1
            # Add unique products to test_product dictionary.
            # print(row[2])
            if row[2] not in test_product_dict:
                test_product_dict[row[1]] = test_product_count
                test_product_count += 1

    return test_user_dict, test_product_dict

In [69]:
test_user_dict, test_product_dict = get_test_users_products('reviews.dev.csv', user_dict, product_dict)

Importing test users and products...


In [70]:
def merged_mtx_products(filename, user_dict, test_product_dict):
    
        print('Creating a matrix with new products on the x axis...')

        num_user_ids = len(user_dict)
        num_product_ids = len(test_product_dict)

        dense_matrix = np.zeros(shape=(num_user_ids, num_product_ids), dtype=np.float32)

        with open(filename, 'r') as train_file:
            matrix_reader = csv.reader(train_file, delimiter=',')
            next(matrix_reader, None)
            for row in matrix_reader:
                dense_matrix[user_dict[row[0]], product_dict[row[1]]] = float(row[2])

        return dense_matrix

In [71]:
merged_matrix_product_rows = merged_mtx_products('reviews.training.shortened.csv', user_dict, test_product_dict)

Creating a matrix with new products on the x axis...


In [72]:
merged_matrix_product_rows.shape

(4426, 36924)

In [73]:
merged_matrix_product_rows

array([[4., 0., 0., ..., 0., 0., 0.],
       [0., 5., 0., ..., 0., 0., 0.],
       [0., 0., 5., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [74]:
sum(merged_matrix_product_rows[-1,:])

2.0

In [75]:
def merged_mtx_users(filename, product_dict, test_user_dict):

        print('Creating a matrix with new users on the x axis...')

        num_product_ids = len(product_dict)
        num_user_ids = len(test_user_dict)

        dense_matrix = np.zeros(shape=(num_product_ids, num_user_ids), dtype=np.float32)

        with open(filename, 'r') as train_file:
            matrix_reader = csv.reader(train_file, delimiter=',')
            next(matrix_reader, None)
            for row in matrix_reader:
                dense_matrix[product_dict[row[1]], user_dict[row[0]]] = float(row[2])

        return dense_matrix

In [76]:
merged_matrix_user_rows = merged_mtx_users('reviews.training.shortened.csv', product_dict, test_user_dict)

Creating a matrix with new users on the x axis...


In [77]:
merged_matrix_user_rows.shape

(4053, 74025)

In [78]:
merged_matrix_user_rows

array([[4., 0., 0., ..., 0., 0., 0.],
       [0., 5., 0., ..., 0., 0., 0.],
       [0., 0., 5., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [79]:
sum(merged_matrix_user_rows[-1, :])

2.0

In [80]:
def to_sparse(filename_prefix, matrix):
    print('Creating a sparse matrix...')
    try:
        # Try loading previously saved sparse matrix from file (becaues I keep crashing my kernel)
        loader = np.load(filename_prefix + '.npz')
        sparse_matrix = csr_matrix((loader['data'], loader['indices'], loader['indptr']), shape=loader['shape'], dtype=np.float32)
        loader.close()
    except:
        # Create sparse matrix from dense matrix, write to file as backup
        sparse_matrix = scipy.sparse.csr_matrix(matrix, dtype=np.float32)
        scipy.sparse.save_npz((filename_prefix + 'npz'), sparse_matrix)
    return sparse_matrix

In [81]:
sparse_merged_matrix_pr = to_sparse('sparse.merged.matrix.pr', merged_matrix_product_rows)

Creating a sparse matrix...


In [82]:
sparse_merged_matrix_pr.dtype

dtype('float32')

In [83]:
sparse_merged_matrix_pr.shape

(4426, 36924)

In [84]:
sparse_merged_matrix_ur = to_sparse('sparse.merged.matrix.ur', merged_matrix_user_rows)

Creating a sparse matrix...


In [85]:
sparse_merged_matrix_ur.shape

(4053, 74025)

In [86]:
def normalize_merged_matrix(sparse_matrix, dense_merged_matrix):

    print('Calculating global mean...')
    global_mean = sparse_matrix.sum()/(sparse_matrix != 0).sum()
    print(global_mean)
    
    print('Calculating row mean...')
    matrix_row_mean = sparse_matrix.sum(1)/(sparse_matrix != 0).sum(1)
    print(matrix_row_mean)

    print('Normalizing the data...')
    normalized_matrix = sparse_matrix.copy()
    normalized_matrix -= matrix_row_mean.reshape(-1, 1)
    
    print('Normalized matrix: ')
    print(normalized_matrix.shape)
    print(normalized_matrix)

    return normalized_matrix, matrix_row_mean, global_mean

In [87]:

normalized_matrix_products, matrix_row_mean_products, global_mean = normalize_merged_matrix(sparse_merged_matrix_pr,
                                                                                            merged_matrix_product_rows)


Calculating global mean...
4.1266
Calculating row mean...
[[4.]
 [5.]
 [5.]
 ...
 [4.]
 [4.]
 [2.]]
Normalizing the data...
Normalized matrix: 
(4426, 36924)
[[ 0. -4. -4. ... -4. -4. -4.]
 [-5.  0. -5. ... -5. -5. -5.]
 [-5. -5.  0. ... -5. -5. -5.]
 ...
 [-4. -4. -4. ... -4. -4. -4.]
 [-4. -4. -4. ... -4. -4. -4.]
 [-2. -2. -2. ... -2. -2. -2.]]


In [88]:

normalized_matrix_users, matrix_row_mean_users, global_mean = normalize_merged_matrix(sparse_merged_matrix_ur,
                                                                                     merged_matrix_user_rows)


Calculating global mean...
4.1266
Calculating row mean...
[[3.83333333]
 [5.        ]
 [5.        ]
 ...
 [4.        ]
 [4.        ]
 [2.        ]]
Normalizing the data...
Normalized matrix: 
(4053, 74025)
[[ 0.16666667 -3.83333333 -3.83333333 ... -3.83333333 -3.83333333
  -3.83333333]
 [-5.          0.         -5.         ... -5.         -5.
  -5.        ]
 [-5.         -5.          0.         ... -5.         -5.
  -5.        ]
 ...
 [-4.         -4.         -4.         ... -4.         -4.
  -4.        ]
 [-4.         -4.         -4.         ... -4.         -4.
  -4.        ]
 [-2.         -2.         -2.         ... -2.         -2.
  -2.        ]]


In [89]:
def compute_svd_from_normalized(normalized_matrix):

    print('Computing svd from de-meaned matrix...')

    U, sigma, Vt = svds(normalized_matrix, k = 100)
    S = np.diag(sigma)

    return U, S, Vt

In [90]:
U_products, S_products, Vt_products = compute_svd_from_normalized(merged_matrix_product_rows)

Computing svd from de-meaned matrix...


In [91]:
predictions_product_rows = np.dot(np.dot(U_products, S_products), Vt_products)-normalized_matrix_products

In [92]:
predictions_product_rows

matrix([[3.82812524e+00, 3.99999994e+00, 4.00000000e+00, ...,
         4.00000000e+00, 4.00000000e+00, 4.00000000e+00],
        [4.99999988e+00, 7.17040359e-14, 5.00000000e+00, ...,
         5.00000000e+00, 5.00000000e+00, 5.00000000e+00],
        [5.00000000e+00, 5.00000000e+00, 8.02348571e-16, ...,
         5.00000000e+00, 5.00000000e+00, 5.00000000e+00],
        ...,
        [4.00000002e+00, 4.00000000e+00, 4.00000000e+00, ...,
         4.00000000e+00, 4.00000000e+00, 4.00000000e+00],
        [4.00000003e+00, 4.00000000e+00, 4.00000000e+00, ...,
         4.00000000e+00, 4.00000000e+00, 4.00000000e+00],
        [1.99999989e+00, 2.00000000e+00, 2.00000000e+00, ...,
         2.00000000e+00, 2.00000000e+00, 2.00000000e+00]])

In [93]:
predictions_product_rows.shape

(4426, 36924)

In [94]:
U_users, S_users, Vt_users = compute_svd_from_normalized(merged_matrix_user_rows)

Computing svd from de-meaned matrix...


In [95]:
predictions_user_rows = np.dot(np.dot(U_users, S_users), Vt_users)-normalized_matrix_users

In [96]:
predictions_user_rows

matrix([[3.66146406e+00, 3.83333333e+00, 3.83333332e+00, ...,
         3.83333333e+00, 3.83333333e+00, 3.83333333e+00],
        [5.00000000e+00, 3.94119260e-18, 5.00000000e+00, ...,
         5.00000000e+00, 5.00000000e+00, 5.00000000e+00],
        [4.99999999e+00, 5.00000000e+00, 2.25611037e-15, ...,
         5.00000000e+00, 5.00000000e+00, 5.00000000e+00],
        ...,
        [4.00000001e+00, 4.00000000e+00, 4.00000000e+00, ...,
         4.00000000e+00, 4.00000000e+00, 4.00000000e+00],
        [4.00000001e+00, 4.00000000e+00, 4.00000000e+00, ...,
         4.00000000e+00, 4.00000000e+00, 4.00000000e+00],
        [2.00000000e+00, 2.00000000e+00, 2.00000000e+00, ...,
         2.00000000e+00, 2.00000000e+00, 2.00000000e+00]])

In [97]:
merged_prediction_matrix = np.zeros(shape=(len(test_user_dict), len(test_product_dict)))

In [98]:
merged_prediction_matrix.shape

(74025, 36924)

In [99]:
for idx, key in enumerate(test_user_dict):
    print(key)

AMFIPCYDYWGVT
A3G602Z4DWDZKS
A33BOYMVG3U58Y
ANEDXRFDZDL18
A1VN7IS16PY024
A1WXH5CI1PDWZZ
A30TK6U7DNS82R
A3DG9QOFBA4PLB
AO3ZVS2A1SZ3Y
AOB5695UUUJ0
A2FSZ0JXOK9O2C
A1R2WP1CMA6O96
AQRODCIYD7PYX
A34GZPHWYPSY2T
ASLTUNWNRTUOY
A195PCNYWRB75
A1R7TXCKWDZNOQ
AI54XO5Z755FH
A1LSDDSM4PGOU5
A1ZZ5CT3036BS7
ATP9LYGM6D3RO
A3CAKEDC4V3LE2
A28V2R9T34X2VU
ANCOMAI0I7LVG
A1BH3LQ2U05OSM
ABDUEJT0GE07
AAAAJPG5Z1TLS
A27H9DOUGY9FOS
A3DVS9Y4Z1HIDJ
A233UR4B7OT4RR
A38H6JROS603PV
A3MEHHL9LNKW4Z
A33WRCAW3ZU2CU
A3OB3WDUN51D8A
A3R6ST52EBN2FK
ARKN5M2UYTF61
A1RECBDKHVOJMW
A2AMFKY99R4BKP
A14JWF5U4EB6DY
AQSQLWD3NLMAS
A3T6OR4CAVJDNW
AI7S94161XV07
A109ME7C09HM2M
AMYW43AHO16SS
ABO2ZI2Y5DQ9T
A6VG20N5PW6UF
A3UEN4PDSLPU16
A3BK1RYLHESYSJ
A134XNZ2TN5PLR
A1LSQ1FQP1FFG0
AQTU8RON0JTY8
A132O2LX94WY9P
A3SFO2GSP5CVSM
A1GN8UJIZLCA59
A2BDZAU0Y4J6NB
A1AFULO1G1A774
AEL6AD2AL2UX8
A92QRB0H76H6A
A2HN2BU4VXBQ3H
A1SLC8Y43ZSTH3
A1DNA1EX759JPY
A1KQ1GR57HRWNU
A328S9RN3U5M68
A2L3KL43DDWVSQ
A6J9LCOY1VRJK
A2HXTZ3JCJ441Y
A2ZU9VVPK18EX9
A1L9MIIBI7409N
AP3B

A2IOEAT7TJLOZL
A2BLHPNPJV6495
A1QDTMOG8ZG8P0
A39GW5CBWTIWAZ
A1AODO5VALHRSL
A2SW6J1SIBA2AK
AI69U88HXU9LC
A16280G4A02REI
AH3Z3AT4OI7WF
A3TNM3C9ENUCFW
AS9K2E5I30D3G
A12A8LU93A132U
AHS680SHZ36GP
A3C2U81W8W7IH9
AMNLUJEUNGC8R
A2SLIV8KOEOSBJ
A3L8R6HQ8JGMKK
A331OF34UX4Y1K
A35YWA2V4QHOJ3
A36FRBJ4QO0RQ3
A26TY6GCGBF5HT
A3PWF2AQ5XYALW
A2YRSGEL0NO8S3
AI48X7SYUXI6K
A1906RZITWT2K2
A1RIX4O3ZRFIYX
A1QJEI2S15711P
A1J2NY8WN0ZQSR
A3AXHKL6GMLJ4P
A2H0T7MSR2LK45
A1ORZ2ZH5MIZCG
AZQ6PYDEJQJEF
AHYB8KRUGQFHL
AIKGPO3AQW1NK
A25MZ7A5A4I6Z5
A1OXSBQA7Y0QEG
A2CPROK4QJ30W4
A1H7Y5XKPGT0OS
A50ZGWCM3RXW1
ATXL536YX71TR
A1GBEG4DK50DAT
A2FTONQP9YG04L
A3SP37JLGH5KFY
A17OA1DWOLKNS6
A39XC9ME16JRK5
A2JVB5VQLOUNAB
A2JUQKAELBG4MI
A2XYBC4PLEQFJ1
A2WZ1B92F81LJJ
AMB4VOUKOFYJM
A13B8UTGS5I9GR
A6XI10G54YAJY
A293HA28PN3VO4
A2PXP8UMMDAGPM
AF5B3K4SX0KHX
A2ZXCWUWXLVK6I
A16LBSWNQRS292
A1FYUCCC8CX1E0
A1Y92XEKKBS93K
A2FVLYFKJSV1WJ
A1RL1L9NY5LLBS
A82MLYSUUU3CF
A1LRC2T7SFATJC
A1SJSORHCD1UAL
A1A3T2KJE8R71U
A1VGVMUOI5FHTE
AXXLISID4UJK7
A1NIPHCQHQ2

A3CXPJJ15E1545
A5ORJWVHTBHFN
A1TR0WPC93BEC8
A1MX6D3JK6IKDW
A3443SUQ5KMPL0
A1E16XOMO94MA
A37DLVPKJZGSQF
A2GOAEF0ZRNG13
A2P9RFHSSHMMCY
A1BX8Z3X6OIMMT
A24MA24TI2GJ20
A181ID9TLBXR3I
AN4YIQO49DHN5
AOBUUZNV6UUK9
A3FVE0A30QIUHN
A347KF6CEMD2CK
A2GCGMIX4KYP5F
A1XV3QLSLGLXL8
ASRSV7OSCMX63
A2ZFAYA9NKP2SA
A1TNW1D90ZWY9M
A1D2WBIBGP2M6H
A3UUAAPRGF2UR2
A22GJ2SRENMZS0
A3RZPMYJUGL1E7
A12G9WIQS05KM8
A2BC9TW5GO4XJR
A2N7338UE4HSKD
A32T9TM5F7KHIG
A35T704GNU6755
A1Z7V65GIRXPIA
ALR35EFI69S5R
ATAWJ0EOWAMZH
A2582KMXLK2P06
A13JDATSL67A47
APZC5PRJVM0PY
A13J1QX56M80PW
A230TFNIMO51UU
AVDIE0V69WKKB
A37UOT2RDW2OVL
A28YDMI499J1X9
ABLOQZIL42W7I
A328547P5BGZC
A3NON4506GPJC0
A3EAFCZUVL6NZ9
A25ZZMC5VB6MC8
A321EEQ906PFKK
A1N5Z3PHTP5YDP
ANC96OOJ46FYS
A1BNMI0S8QOMXV
A2TSGJFQ5LYQE0
AVU3JRLDRUCS9
A1ZH9LWMX5UCFJ
A1ZBGFVVMDPOPD
AYY56CYWR2VM7
A210UC2E7OXZYG
A3BIQJELLFEGIA
A2DK0GIEEWPJF4
A1MQQEM7W77L62
A2QD9YMS8TMTWN
A1YUA1ZMB2Q1XJ
A21C4LOJL6QGMD
A2800DZRKFY5JZ
A32NCBR8D0XLWC
A123797SICR4N0
A3VQSFORKH8B7O
AWOR72TWT6CA2
A2T2A4YSJ9

A31ZRZWBVUQQV8
ABS6VJX1KCAW4
A2Q2YJHBYV8T2D
A3M3PTFA1ACPGT
A3IPIC6UHJ1T9X
A3DLCY98104CGF
ARP9PH6O7H2WC
AV1KZN5VUVU4O
A2V5R832QCSOMX
A1Y7EKXFKOFTN0
A1NUJNTPV1Y11T
A2Z7AHF9W2VYCZ
AUY6OZTQM4YE6
A108GN269S733W
A1537KCD6LBWGI
ABD6TPKC6ADF4
A29IQ30LWVK0YT
A3PVSNS17HCIXN
A2UE4JYRSV11QX
A1YX6YUHJA11KE
A3ANO8MT4P12D8
A3L8XRYMLZZES6
A2MYUI8IT6UBUU
A1F72LRP98VC96
A3JWR2O1MZ7VNE
A3VWSFFQKBU9LD
A18A3H566K45D9
ARYPK3ZRXTGWB
A238W7T3KJAKQH
APMKMM6284FH4
A2ZVERVFM25MJT
A2SW2A3PE5RUQE
A2MDL0OV4AMTPM
A2DWG1QNHOS3OK
A383P7YNLSINC0
A1TUKDEBTP4IC1
A3ALJT9CJBMZWS
AOTMP0OKJOUWI
A15MLF38WROSWU
A2PACRCFW1CXD2
AIXGFTIK2K3TT
A1HHU3I9M83YBV
A3QEPSZ62L6BU5
AFR7TYM9E3V8Z
A35T4V64J4AIB9
A3EOYN87MMNHL1
A2UUW8TDBG41O2
A1BYDMYY2EDVRF
A2ASHKXP5AJTXY
A267U5ACM1VWHW
A1EJU2M8UQF7XN
A3RJ23YYGNJXXW
A5WMBIOGE8Q6N
A2U6VP21H9UVV3
A13PSNTSS4T0C0
A1BKGGKR8FI97M
A3V3CABG8BH9F2
A2QVQEF7RK74FX
A2PAB38MSSTWK4
A188LOA4EPLIKV
A2M5FI4CB6VUXF
A17UIQFPP6R9CS
A21K28EQ023UUU
ASY5VID9J91KX
A2ZAV3XAGG894J
A2Y3CWITEF9JGY
A1OP6TUBG3OGEN
A31KQUQ

AV0U7V69P8IX
A1PW55KKYM78D6
A3DSTPJCK1IGA5
A3ISYWMAOHDYY7
A1GVZ7ZW27R1LX
A2CVP31XTYSZFE
A3H1H826N53BDO
A3BZMYFG6UF8G8
AD4K58W3ZBI9M
A3GE7G3D8W7T01
A16RE8HUDF35GE
A2U80IPZXN5V1U
A33H8DC3ZG58T0
AJBVOWKRNT9CS
A1EJT7NW91NWMP
A9KD6LJPKKHJT
A3J9JNU7G32U0V
A2VNDUY7NUHOUV
A3N8RZSXKN1OR2
A37H9L4DWOWST9
A1WYHRY9WRWLQ3
A373LY69LKT8CA
A2Q5K1G3S8RLWX
A258VEL0TZFBQM
A30GDJPDPHZRT7
A1G9FX1KV45N41
AH36YZ40JMCSN
A45XJPVTK0Q94
A20YLPT92ITUIZ
A2BJJ6MKIC1ZZ1
APJGF9K5JNTFB
A1G5LJ8T1IGYC5
A3QTB346UKG6TV
A29QBRBXYVKV8Y
ABYNIQUEMDKY6
ANLEL1J3ZS8YP
AC09OIFJYTUQK
A3QJKYZ4R2MFW1
A1SEJQQTN6H9IV
A3MU0PLWG9VQVV
AY6A8KPYCE6B0
A2MLNA51TLF425
A3H1NI0FSDFMWX
A2QW2V285U824L
A3BAOIC7JMCY6R
AA9DTQQPE45Z2
A38DIPWA345AEF
A13FBJ5DU6PJRK
A34DPXEGCFNZF4
A3NE60T6QINREM
A2N1MWCIAHKBHN
A2CZBGIJP8TZ1T
A3IGA729Q3AB5V
A1KT1GWCW8F80
A34IBXM7E8CPWE
AMG2LF8MLUDN1
A1N0LCPR7O7OLL
A382QAPOIP4Q8S
A11MGPEYU3VO1U
A3OMDSHIGTFY84
ANNHSAZXB72KH
AMMXFNJSKJUQ
A1U6E8IJEATCYM
A1EAJBI1J460G1
A3QZ65PZYWP5UR
A2DOPZR0ZONSMO
AHIK7BUXFRMT8
A3CAS1BYPWLSD6

...

A38X5C9PMCTJHQ
A5LK5ZWKQ6SYQ
A1FKZ7W5QAX6LD
A22TI0EKLA6XCR
A3RE9LOZZLZ3O
A2BQ2H26EXT0X9
AAO8I603A38ZE
AEJZOEN2JVWAB
A11M77A5ENIGDO
A1JGNUNKASSJWQ
AUMFK2X8NJPM6
A3TOQAMJURAYFC
A1KL7GCWLQT3MV
A3M9HH5BWG7G0F
A1GYCILLXA6T2L
AT2BNHAUJIHRY
A153J09XKRKLFE
A1D6UZRNWYXN27
A2Z8VYD0LAP8Z
A1SWR7ZHXSBJL0
A2K2T6XP3WY2QH
A2W1GT509PD228
A2RC6LVEFW0NU7
A29MT1LOZZQH9S
A3DHVN6AN5X5UT
AKJVKYX014LY2
A3BRV5J15826WG
A3DYV2V3BXZFI
A3SUBHQ6PZ4RHQ
A14JRNU2JVRBPA
ACFKYPSBPKF3W
A21NJYLCBTVXOJ
A16PH7GJU2D804
AFDHYHC7ZIWG3
A17OPA6OHZ4GYG
A2X2A43L6ULPD3
A31AY0PVU5V8OG
AOR7KPK86V6I0
A2VGAZHMWIWILK
A2HX18SCXF7AY0
A26ZDF3062SJVR
A1XMXEREXXOVWP
AQI9DAK2CX2B9
A10ZKOZ7DOMXMR
A3IAH0N18LDXLP
A2A0O6XMPUFFTC
AK7GDJRM33C6I
A1WJ193ZI7TK3J
A32CV29ZQ4D77J
A3QTL2I4K5NEYG
A34EO1E25LWDZV
A22M0WFA2Z62YR
A2YNL79E3AY3AZ
A2UHHEP0J237RU
AY0LH0FUV88H7
A24NSMJ6CLIGYS
AFDQ7QHDYES5E
A2NG313A8LTHS9
ARI3L8MRDCOJO
A2KXK7CXADAPVI
A35QGTNWJTRGUG
A31BJMQUUFDI2A
A2GD7NZLWL0TSA
A1JH9KIF5KIF6G
A1BXZEMPRYNGN0
A127XOISJIWZS1
A1Q0YL2840G6NH
A3X3TTEUMW9D

A3HLAG7T2JSPAK
A2YQVH5XGGWBHP
ARV2ZLVGV1LBS
A1D50XFXDM24A1
A1VXO8FQ4GAFUO
A17R9VYDIIBL2K
A33065VK2M1DGE
A17SD0E4QSTJMG
A2Y9NHRLWUUC6W
A25NX2427TSKSU
A11QVZLUPZ5OA
A3TW2UQDU2PGN3
AX148M3X6EUGN
AJ1EXYNNIKCTQ
A2EOJ3JU97GIX4
A69MW0GU6Y95I
A1KTQEX4RWWL8Q
A2G742BCMKQWBX
A1NECG4UNVOPWJ
AZ425ZQZNKYP2
A3B1GE37ASB8OL
A2NEG1ST5UP7UK
A1YS7DE1B78UC8
AO8CXSAMUTOUL
A3JG8IW8QYDV56
ASSS5KQQMJ1YP
A1LB5OUZ3N12BV
A3MUREPAHLVDRI
AL8NSGE6MUB19
A2X2BD7OVQEFVI
A2RO5BKNBR7BSR
A37SE85JEI8ZK6
A1GSHPYC3QQ8XC
A1ZXZ2ND3R1C0R
A2P5RA47WMV9RS
A2OYE80BLPGEQ2
A3SLMF7XFN109
A2FGC6GK4TIA4P
A3K3AZQ1KWPWRZ
A12GNFQAM60C1B
A26GMJ3MXGO2ZY
A30OJW52VK78W3
A267QFWPG5DJMM
A2C289O6K9IIJU
A3GH6ZA8XIPWV6
A53T185PYUJKZ
A2K3WCDBOH5YYG
ANM4I38VRP1VR
A3AU8MMDVQTA0D
AX52ULYSK82AF
A21O4GI265ACK8
A3S9MW9SHVKCVU
A1VJALJYVIM6OH
A2P39PK2Q3EJ05
A26IXKSKY76T10
A1YC38QJ6EKLWX
ABO5QNKTIZNN5
A2CMJNIM616T9L
A1ART9CIZ02WSN
A25HIZKN80O2PG
ARLKXEBSYLU6B
ARX9I48V4EZAU
A2X64F7DOMZO23
A6B8EN9A9X7GU
A3TS8OH2DCMOE9
A3013MHSQS4Y8Y
ASJXBNCRYNIKU
AH39OFADI4W11

A21N20QGFUWFEC
A2H2AJY184XDS3
A2G3PISSQWDXRK
A1UNTOR05GP659
A1DH3496NU4EKQ
AAX7MN9KCR2IY
A1205P90DWZYOX
A2CPJSPVHVP2DN
A3AW4F2JZZTRWN
A9MCIKXY486RL
ASMA5SVT9SDWN
AT2Q5KL70OI4A
AH7UU6U314P0M
A3VGZNP9QAHF1B
A1DER6XEQ1W2KD
A26JJGCRI9RSBH
A3KIOOXQM0R6NA
A5FKM5A7UREY6
A1CM7N4368HGZ6
A31TL0DN1CNG8B
A2K8LG0NQ7W5X0
AYYB7Q968A82W
A2IENUXYYYD9PU
A2V79Y19V2OO2O
AG2YXYIQ8TLTA
A2OIQ3JGLFXHUX
A306LIMEW2K2RV
AYDSX1WZ4NU17
AW24ODXPY9CMI
A1XD4DB51KEJFP
A13SMNS5QLSC9Y
A3VO0WDV1N3OSV
A2CZPKUETRA9LO
A3LJTMT2WB7Y3P
A1WXV2M71VH7TH
AKMY377OSFWA6
A9AI9WH600I1I
A1PIXT15FZKB8P
A3BFKY618DR43K
A3I7NIXOKQJE21
A2XPFE1NUH3NJ0
A2N3GV82UDP5M5
ABXY63NKJLSYN
A1SFZXPPJKZAVY
A1MIUJ82KM4BKI
ANQSTR7N9C54E
A3MYENIMW2LEMG
A1H5IAUCZVTZYK
A19NSYIFT2GNNW
A2LHJTT1FT7XRD
A2RM35LBS0XE58
A431Z0C4X1K35
A2PN9CINNJ46KH
A1C3AIGVSD0TB1
A36DG7X9TM6NZ6
A3SH7DJ935555N
A30EVBEMK0X30J
A2TTFY3Z2XVDHN
A3RQB2W820QCZA
A3U6L3FI2AEJNT
A1AFS8NFB1O02V
A1NGNQHOKPBFP3
A2F2GLVFRNV7JJ
A2IPM9EW3CBAY3
A20PWDSOILLT5I
A2IS1BEP1RJJQ4
A63ALOKUS9XHG
A28Q9BSUOWJ

A3DHRFCSFGJPIW
A4EJY8RXRHNWO
AM67VZ3Z4HUTR
A3UBCX8K6LP1OM
A1CW2XQP3IV0NZ
A3M8E27LZXKVM3
AVO6W8X22BH8Q
AS56N6FYEQ12U
AV7N3NQND9O12
A1RP1ZHLOOO8C9
A12Y6NKSL8KYSM
A2BU0FDY5V0Y9T
A2HVFBVT0X1IP1
A1G199WJVWNCSL
AQNP6RI4QY5UI
A1NENDUY6T73Q9
A3SFP0W59HQZG3
A385STDS7VYKPH
A16JVTE1LVDCBX
A3IC02PU1BELQ1
A314VFXKS01GGC
A3I989CW5E1E52
A385Y8KNR982TL
A21Q1LBZP2671X
A3TMR5FI9TQDQ1
A17KOHZ01LKWCS
A3L238KOMKJL00
ANF45HZVC102O
A3NU4SH79JISAU
A2WINIVCAYK5H5
A1L4FASS0WUMWJ
A1H4VEKCLCPF22
A15MGXARG5GJZY
AQ4WS7I2LYTOX
A369RL90GFAO9K
A210SPRGOOG2D0
A3OSR92LFD75EG
A2X5LFVFOHOOXX
A37ZHD149TT7MY
A2BIC4KOGEG8L5
A1DVSAJMHYJKNR
AZML6X7KX7D33
A2UYKZHBTHPFVG
A1Q5QDUQZK1H3C
A2WEGRHD0XQAFE
A1L74FOIY39OO0
AE7QFYA9VLFF2
A2OSLVUZ91CM15
A1YNUXRE39VOMF
A12L4JHS4WWI1U
A3A0DXA6GCIK4Z
AQ2VUOU6BOA93
A2LWDNKQZOR2A7
A2TRO2N8EFD2LJ
AVVYP3GUIY011
AWPD4QOG50UYT
A16OY5QSGBWJCO
APA6QGSK5S8HA
APUOCPHDG6B4H
A1995LC19L5BE2
A3L977U40T2FM3
AVHE883R6FCEB
AVI7WGFMF7GAJ
A2XYUUR8XKG1E2
A15FJK2UH6OHXT
A2HDUL2YFE5NR9
A3RBEESTJUZQ6D
AQXX46012LVO

A15GTCK2TKSLFY
A2JKDKZ6FFIFGA
A33FJFVRY9570Z
A1XYT4WO34OQ6O
A2SNM8LWUHZVV5
A3Q7C0V12LS2WF
A2SU6CA6HSK85I
AGZWKQJB1HRPQ
A3SREAGODFQG1C
A2K6Z2IN9HUT5B
A2Z0I41FWHXEC5
A3P5YO42UCQHZH
A164FHLT61U69A
AHNT97DWEAQUY
A1EGVO0138ZR7O
A2B4BYXDYD63ZC
A2XOBPGHXKVQWS
A3TN3R1BV4VBZT
ADG865L3QRSFT
A2L7N2U5Z316ZE
A1MMVPXI5B8AGQ
A1LJK60TZNO5N5
A1Y9HYZNBMMX4B
AW9QUE6II6LC2
A2BXTKDXE61DNF
A1R38258EUZBZE
AW9THCOAE9A95
A1ZQREPBYQ32S9
A2GS6PSTFMAHK6
A1ACVI6VRMU5M4
AGW4PTW7LGE8F
A216WX511ULMEI
A3CJ3F232QXQHB
A30GT6HHQD2AHV
A3BF6PA5ZVH30S
A2727C1VHMXRT1
APZXY2P25Q512
A3P6VDZ534M3YX
A3UM51F3L81CNH
A10EH0HZKO2KOP
AWF1L8FQG6M1G
A3UU7QX6HXKU7S
AYYD8V2A2QJ71


In [100]:
prediction = predictions_user_rows[0]

In [101]:
prediction[0, 0]

3.661464055379232

In [104]:
def query_normalized_matrix_test(test_file, prediction_file, test_user_dict, test_product_dict,
                                predictions_product_rows, predictions_user_rows, global_mean):

    print('Reconstructing matrix and making predictions...')

    with open(test_file, 'r') as test_file:
        test_reader = csv.reader(test_file, delimiter=',')
        next(test_reader, None)
        with open(prediction_file, 'w') as outfile:
            outfile_reader = csv.writer(outfile, delimiter=',')
            outfile_reader.writerow(['datapointID', 'overall', 'prediction'])

            for row in test_reader:

                try: 
                    # Query by user (new products on x axis).
#                     product_query = predictions_product_rows[test_user_dict[row[1]]]
#                     prediction = product_query[0, test_product_dict[row[2]]]
                    prediction = global_mean
                    outfile_reader.writerow([row[1], row[0], prediction])
#                     print('Query by USER')
                    print(prediction)
#                 # Query by product.
#                     product_query = predictions_user_rows[test_product_dict[row[2]]]
#                     prediction = product_query[0, test_user_dict[row[1]]]
#                     outfile_reader.writerow([row[0], prediction])
#                     print('Query by PRODUCT')
#                     print(prediction)
                except:
                    try:
                        # Query by product.
                        product_query = predictions_user_rows[test_product_dict[row[2]]]
                        prediction = product_query[0, test_user_dict[row[1]]]
                        outfile_reader.writerow([row[1], row[0], prediction])
                        print('Query by PRODUCT')
                        print(prediction)
#                         # Query by user (new products on x axis).
#                         product_query = predictions_product_rows[test_user_dict[row[1]]]
#                         prediction = product_query[0, test_product_dict[row[2]]]
#                         outfile_reader.writerow([row[0], prediction])
#                         print('Query by USER')
#                         print(prediction)
                    except:
                        # If no matching users or products are found, make prediction based on global mean.
                        prediction = global_mean
                        outfile_reader.writerow([row[1], row[0], prediction])
                        print('No matching query: GLOBAL MEAN')
                        print(prediction)

    print('Done.')
    return None

In [105]:
predicted_ratings = query_normalized_matrix_test('reviews.dev.csv', 'reviews.dev.labeled.csv',
                                                test_user_dict, test_product_dict, predictions_product_rows,
                                                predictions_user_rows, global_mean)

Reconstructing matrix and making predictions...
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266


4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266

4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266

4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266

4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266

...

4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266

4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266

4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266

4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266

4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266
4.1266